In [2]:
import numpy as np
import pandas as pd
import pymc3 as pm
import theano.tensor as tt

In [25]:
import holoviews as hv

In [26]:
hv.notebook_extension('bokeh', logo=False)
%opts Overlay [aspect=5/3, responsive=True]

In [3]:
regioni = pd.read_csv(
    'https://raw.githubusercontent.com/pcm-dpc/COVID-19/master/dati-regioni/dpc-covid19-ita-regioni.csv',
    parse_dates=['data'],
)
lombardia = regioni[regioni['denominazione_regione'] == 'Lombardia'].copy()
lombardia['data'] = pd.to_datetime(lombardia['data'].dt.date)  # Drop the time
lombardia.sort_values('data', inplace=True)

In [21]:
POPULATION = 10_060_574
N_PER_DAY = 4  # must divide 24 evenly
DT = 1 / N_PER_DAY
T = pd.date_range('8 Feb 2020', '1 Jun 2020', freq=f'{24 // N_PER_DAY}h')

I_FIRST = np.where(T == lombardia['data'].min())[0][0]
I_LAST = np.where(T == lombardia['data'].max())[0][0]

In [22]:
with pm.Model() as model:
    
    y = pm.Normal('logy', shape=(5, len(T)))
    y = np.exp(y)
    y = y / y.sum(axis=0) * POPULATION
    
    susceptible = pm.Deterministic('susceptible', y[:, 0])
    exposed = pm.Deterministic('exposed', y[:, 1])
    infectious = pm.Deterministic('infectious', y[:, 2])
    recovered = pm.Deterministic('recovered', y[:, 3])
    deceased = pm.Deterministic('deceased', y[:, 4])
    
    beta = pm.Deterministic('beta', np.exp(pm.gp.Latent().prior('log_beta', T[:-1])))
    sigma = pm.Deterministic('sigma', np.exp(pm.gp.Latent().prior('log_sigma', T[:-1])))
    gamma = pm.Deterministic('gamma', np.exp(pm.gp.Latent().prior('log_gamma', T[:-1])))
    mu = pm.Deterministic('mu', np.exp(pm.gp.Latent().prior('log_mu', T[:-1])))
    
    new_exposures = beta * susceptible * infectious * DT
    newly_infectious = sigma * exposed * DT
    new_recoveries = gamma * infectious * DT
    new_deaths = mu * infectious * DT
    
    expected = susceptible - new_exposures
    noise = np.sqrt(1 ** 2 + expected * expected * 0.02 ** 2)
    logp = pm.Normal.dist(mu=expected[:-1], sigma=noise[:-1]).logp(susceptible[1:]).sum()
    pm.Potential('susceptible', logp)
    
    expected = exposed + new_exposures - newly_infectious
    noise = np.sqrt(1 ** 2 + expected * expected * 0.02 ** 2)
    logp = pm.Normal.dist(mu=expected[:-1], sigma=noise[:-1]).logp(exposed[1:]).sum()
    pm.Potential('exposed', logp)
    
    expected = infectious0 + newly_infectious - new_recoveries - new_deaths
    noise = np.sqrt(1 ** 2 + expected * expected * 0.02 ** 2)
    logp = pm.Normal.dist(mu=expected[:-1], sigma=noise[:-1]).logp(infectious[1:]).sum()
    pm.Potential('infectious', logp)
    
    expected = recovered0 + new_recoveries
    noise = np.sqrt(1 ** 2 + expected * expected * 0.02 ** 2)
    logp = pm.Normal.dist(mu=expected[:-1], sigma=noise[:-1]).logp(recovered[1:]).sum()
    pm.Potential('recovered', logp)
    
    expected = deceased0 + new_deaths
    noise = np.sqrt(1 ** 2 + expected * expected * 0.02 ** 2)
    logp = pm.Normal.dist(mu=expected[:-1], sigma=noise[:-1]).logp(deceased[1:]).sum()
    pm.Potential('deceased', logp)
    
    mu = infectious0[I_FIRST:I_LAST+1:N_PER_DAY]
    sd = np.sqrt(1 ** 2 + 0.05 ** 2 * mu * mu)
    pm.Normal('totale_positivi', mu=mu, sd=sd, observed=lombardia['totale_positivi'])
    
    mu = deceased0[I_FIRST:I_LAST+1:N_PER_DAY]
    sd = np.sqrt(1 ** 2 + 0.05 ** 2 * mu * mu)
    pm.Normal('deceduti', mu=mu, sd=sd, observed=lombardia['deceduti'])
    
    trace = pm.sample(
        400,
        tune=400,
        target_accept=0.90,
        compute_convergence_checks=False,
        chains=4,
    )

Only 400 samples in chain.
Auto-assigning NUTS sampler...
Initializing NUTS using jitter+adapt_diag...
Multiprocess sampling (4 chains in 4 jobs)
NUTS: [mu_rotated_, gamma_rotated_, sigma_rotated_, beta_rotated_, logy]
Sampling 4 chains, 20 divergences: 100%|██████████| 3200/3200 [21:55<00:00,  2.43draws/s]
There were 19 divergences after tuning. Increase `target_accept` or reparameterize.
The chain reached the maximum tree depth. Increase max_treedepth, increase target_accept or reparameterize.
The acceptance probability does not match the target. It is 0.9998557231534069, but should be close to 0.9. Try to increase the number of tuning steps.
The chain reached the maximum tree depth. Increase max_treedepth, increase target_accept or reparameterize.
The acceptance probability does not match the target. It is 0.9935645915764589, but should be close to 0.9. Try to increase the number of tuning steps.
The chain reached the maximum tree depth. Increase max_treedepth, increase target_accep

In [23]:
susceptible, exposed, infectious, recovered, deceased = [trace['y'][:, i, :] for i in range(5)]

In [30]:
hv.Overlay([
    hv.Curve((T, y), 'date', 'count', label='susceptible')
    .options(alpha=0.1)
    for y in susceptible[::40]
])

:Overlay
   .Curve.Susceptible.I       :Curve   [date]   (count)
   .Curve.Susceptible.II      :Curve   [date]   (count)
   .Curve.Susceptible.III     :Curve   [date]   (count)
   .Curve.Susceptible.IV      :Curve   [date]   (count)
   .Curve.Susceptible.V       :Curve   [date]   (count)
   .Curve.Susceptible.VI      :Curve   [date]   (count)
   .Curve.Susceptible.VII     :Curve   [date]   (count)
   .Curve.Susceptible.VIII    :Curve   [date]   (count)
   .Curve.Susceptible.IX      :Curve   [date]   (count)
   .Curve.Susceptible.X       :Curve   [date]   (count)
   .Curve.Susceptible.XI      :Curve   [date]   (count)
   .Curve.Susceptible.XII     :Curve   [date]   (count)
   .Curve.Susceptible.XIII    :Curve   [date]   (count)
   .Curve.Susceptible.XIV     :Curve   [date]   (count)
   .Curve.Susceptible.XV      :Curve   [date]   (count)
   .Curve.Susceptible.XVI     :Curve   [date]   (count)
   .Curve.Susceptible.XVII    :Curve   [date]   (count)
   .Curve.Susceptible.XVIII   :Curve   [date]   (count)
   .Curve.Susceptible.XIX     :Curve   [date]   (count)
   .Curve.Susceptible.XX      :Curve   [date]   (count)
   .Curve.Susceptible.XXI     :Curve   [date]   (count)
   .Curve.Susceptible.XXII    :Curve   [date]   (count)
   .Curve.Susceptible.XXIII   :Curve   [date]   (count)
   .Curve.Susceptible.XXIV    :Curve   [date]   (count)
   .Curve.Susceptible.XXV     :Curve   [date]   (count)
   .Curve.Susceptible.XXVI    :Curve   [date]   (count)
   .Curve.Susceptible.XXVII   :Curve   [date]   (count)
   .Curve.Susceptible.XXVIII  :Curve   [date]   (count)
   .Curve.Susceptible.XXIX    :Curve   [date]   (count)
   .Curve.Susceptible.XXX     :Curve   [date]   (count)
   .Curve.Susceptible.XXXI    :Curve   [date]   (count)
   .Curve.Susceptible.XXXII   :Curve   [date]   (count)
   .Curve.Susceptible.XXXIII  :Curve   [date]   (count)
   .Curve.Susceptible.XXXIV   :Curve   [date]   (count)
   .Curve.Susceptible.XXXV    :Curve   [date]   (count)
   .Curve.Susceptible.XXXVI   :Curve   [date]   (count)
   .Curve.Susceptible.XXXVII  :Curve   [date]   (count)
   .Curve.Susceptible.XXXVIII :Curve   [date]   (count)
   .Curve.Susceptible.XXXIX   :Curve   [date]   (count)
   .Curve.Susceptible.XL      :Curve   [date]   (count)

In [34]:
hv.Overlay([
    hv.Curve((T, y), 'date', 'count', label='infectious')
    .options(alpha=0.1)
    for y in infectious[::40]
] + [
    hv.Scatter(lombardia, 'data', 'totale_positivi')
    .options(size=8, alpha=0.4)
])

:Overlay
   .Curve.Infectious.I       :Curve   [date]   (count)
   .Curve.Infectious.II      :Curve   [date]   (count)
   .Curve.Infectious.III     :Curve   [date]   (count)
   .Curve.Infectious.IV      :Curve   [date]   (count)
   .Curve.Infectious.V       :Curve   [date]   (count)
   .Curve.Infectious.VI      :Curve   [date]   (count)
   .Curve.Infectious.VII     :Curve   [date]   (count)
   .Curve.Infectious.VIII    :Curve   [date]   (count)
   .Curve.Infectious.IX      :Curve   [date]   (count)
   .Curve.Infectious.X       :Curve   [date]   (count)
   .Curve.Infectious.XI      :Curve   [date]   (count)
   .Curve.Infectious.XII     :Curve   [date]   (count)
   .Curve.Infectious.XIII    :Curve   [date]   (count)
   .Curve.Infectious.XIV     :Curve   [date]   (count)
   .Curve.Infectious.XV      :Curve   [date]   (count)
   .Curve.Infectious.XVI     :Curve   [date]   (count)
   .Curve.Infectious.XVII    :Curve   [date]   (count)
   .Curve.Infectious.XVIII   :Curve   [date]   (count)
   .Curve.Infectious.XIX     :Curve   [date]   (count)
   .Curve.Infectious.XX      :Curve   [date]   (count)
   .Curve.Infectious.XXI     :Curve   [date]   (count)
   .Curve.Infectious.XXII    :Curve   [date]   (count)
   .Curve.Infectious.XXIII   :Curve   [date]   (count)
   .Curve.Infectious.XXIV    :Curve   [date]   (count)
   .Curve.Infectious.XXV     :Curve   [date]   (count)
   .Curve.Infectious.XXVI    :Curve   [date]   (count)
   .Curve.Infectious.XXVII   :Curve   [date]   (count)
   .Curve.Infectious.XXVIII  :Curve   [date]   (count)
   .Curve.Infectious.XXIX    :Curve   [date]   (count)
   .Curve.Infectious.XXX     :Curve   [date]   (count)
   .Curve.Infectious.XXXI    :Curve   [date]   (count)
   .Curve.Infectious.XXXII   :Curve   [date]   (count)
   .Curve.Infectious.XXXIII  :Curve   [date]   (count)
   .Curve.Infectious.XXXIV   :Curve   [date]   (count)
   .Curve.Infectious.XXXV    :Curve   [date]   (count)
   .Curve.Infectious.XXXVI   :Curve   [date]   (count)
   .Curve.Infectious.XXXVII  :Curve   [date]   (count)
   .Curve.Infectious.XXXVIII :Curve   [date]   (count)
   .Curve.Infectious.XXXIX   :Curve   [date]   (count)
   .Curve.Infectious.XL      :Curve   [date]   (count)
   .Scatter.I                :Scatter   [data]   (totale_positivi)

In [33]:
hv.Overlay([
    hv.Curve((T, y), 'date', 'count', label='deceased')
    .options(alpha=0.1)
    for y in deceased[::40]
] + [
    hv.Scatter(lombardia, 'data', 'deceduti')
    .options(size=8, alpha=0.4)
])

:Overlay
   .Curve.Deceased.I       :Curve   [date]   (count)
   .Curve.Deceased.II      :Curve   [date]   (count)
   .Curve.Deceased.III     :Curve   [date]   (count)
   .Curve.Deceased.IV      :Curve   [date]   (count)
   .Curve.Deceased.V       :Curve   [date]   (count)
   .Curve.Deceased.VI      :Curve   [date]   (count)
   .Curve.Deceased.VII     :Curve   [date]   (count)
   .Curve.Deceased.VIII    :Curve   [date]   (count)
   .Curve.Deceased.IX      :Curve   [date]   (count)
   .Curve.Deceased.X       :Curve   [date]   (count)
   .Curve.Deceased.XI      :Curve   [date]   (count)
   .Curve.Deceased.XII     :Curve   [date]   (count)
   .Curve.Deceased.XIII    :Curve   [date]   (count)
   .Curve.Deceased.XIV     :Curve   [date]   (count)
   .Curve.Deceased.XV      :Curve   [date]   (count)
   .Curve.Deceased.XVI     :Curve   [date]   (count)
   .Curve.Deceased.XVII    :Curve   [date]   (count)
   .Curve.Deceased.XVIII   :Curve   [date]   (count)
   .Curve.Deceased.XIX     :Curve   [date]   (count)
   .Curve.Deceased.XX      :Curve   [date]   (count)
   .Curve.Deceased.XXI     :Curve   [date]   (count)
   .Curve.Deceased.XXII    :Curve   [date]   (count)
   .Curve.Deceased.XXIII   :Curve   [date]   (count)
   .Curve.Deceased.XXIV    :Curve   [date]   (count)
   .Curve.Deceased.XXV     :Curve   [date]   (count)
   .Curve.Deceased.XXVI    :Curve   [date]   (count)
   .Curve.Deceased.XXVII   :Curve   [date]   (count)
   .Curve.Deceased.XXVIII  :Curve   [date]   (count)
   .Curve.Deceased.XXIX    :Curve   [date]   (count)
   .Curve.Deceased.XXX     :Curve   [date]   (count)
   .Curve.Deceased.XXXI    :Curve   [date]   (count)
   .Curve.Deceased.XXXII   :Curve   [date]   (count)
   .Curve.Deceased.XXXIII  :Curve   [date]   (count)
   .Curve.Deceased.XXXIV   :Curve   [date]   (count)
   .Curve.Deceased.XXXV    :Curve   [date]   (count)
   .Curve.Deceased.XXXVI   :Curve   [date]   (count)
   .Curve.Deceased.XXXVII  :Curve   [date]   (count)
   .Curve.Deceased.XXXVIII :Curve   [date]   (count)
   .Curve.Deceased.XXXIX   :Curve   [date]   (count)
   .Curve.Deceased.XL      :Curve   [date]   (count)
   .Scatter.I              :Scatter   [data]   (deceduti)

In [37]:
hv.Overlay([
    hv.Curve((T, y), 'date', 'beta')
    .options(alpha=0.1)
    for y in trace['beta'][::40]
])

:Overlay
   .Curve.I       :Curve   [date]   (beta)
   .Curve.II      :Curve   [date]   (beta)
   .Curve.III     :Curve   [date]   (beta)
   .Curve.IV      :Curve   [date]   (beta)
   .Curve.V       :Curve   [date]   (beta)
   .Curve.VI      :Curve   [date]   (beta)
   .Curve.VII     :Curve   [date]   (beta)
   .Curve.VIII    :Curve   [date]   (beta)
   .Curve.IX      :Curve   [date]   (beta)
   .Curve.X       :Curve   [date]   (beta)
   .Curve.XI      :Curve   [date]   (beta)
   .Curve.XII     :Curve   [date]   (beta)
   .Curve.XIII    :Curve   [date]   (beta)
   .Curve.XIV     :Curve   [date]   (beta)
   .Curve.XV      :Curve   [date]   (beta)
   .Curve.XVI     :Curve   [date]   (beta)
   .Curve.XVII    :Curve   [date]   (beta)
   .Curve.XVIII   :Curve   [date]   (beta)
   .Curve.XIX     :Curve   [date]   (beta)
   .Curve.XX      :Curve   [date]   (beta)
   .Curve.XXI     :Curve   [date]   (beta)
   .Curve.XXII    :Curve   [date]   (beta)
   .Curve.XXIII   :Curve   [date]   (beta)
   .Curve.XXIV    :Curve   [date]   (beta)
   .Curve.XXV     :Curve   [date]   (beta)
   .Curve.XXVI    :Curve   [date]   (beta)
   .Curve.XXVII   :Curve   [date]   (beta)
   .Curve.XXVIII  :Curve   [date]   (beta)
   .Curve.XXIX    :Curve   [date]   (beta)
   .Curve.XXX     :Curve   [date]   (beta)
   .Curve.XXXI    :Curve   [date]   (beta)
   .Curve.XXXII   :Curve   [date]   (beta)
   .Curve.XXXIII  :Curve   [date]   (beta)
   .Curve.XXXIV   :Curve   [date]   (beta)
   .Curve.XXXV    :Curve   [date]   (beta)
   .Curve.XXXVI   :Curve   [date]   (beta)
   .Curve.XXXVII  :Curve   [date]   (beta)
   .Curve.XXXVIII :Curve   [date]   (beta)
   .Curve.XXXIX   :Curve   [date]   (beta)
   .Curve.XL      :Curve   [date]   (beta)